In [80]:
from espnet2.bin.asr_inference import Speech2Text
from espnet2.bin.asr_align import CTCSegmentation
import soundfile
import pandas as pd

In [81]:
import torch
torch.set_num_threads(1)

## Load model

In [82]:
speech2text = Speech2Text("exp/config.yaml", "exp/valid.acc.ave_10best.pth")

## Load example audiofile to transcribe

In [92]:
speech, rate = soundfile.read("example_audio/emt16k.wav")
assert rate == 16000

In [93]:
%time text, *_ = speech2text(speech)

CPU times: user 3.67 s, sys: 191 ms, total: 3.87 s
Wall time: 3.86 s


In [94]:
print(text[0])

mina tahaksin homme täna ja homme kui saanud on kui krampsumas ise veiki panna


In [116]:
!soxi example_audio/emt16k.wav


Input File     : 'example_audio/emt16k.wav'
Channels       : 1
Sample Rate    : 16000
Precision      : 16-bit
Duration       : 00:00:12.74 = 203815 samples ~ 955.383 CDDA sectors
File Size      : 408k
Bit Rate       : 256k
Sample Encoding: 16-bit Signed Integer PCM



## Example token level alignment

In [95]:
aligner = CTCSegmentation("exp/config.yaml", "exp/valid.acc.ave_10best.pth" , kaldi_style_text=False, blank_transition_cost_zero=True)
segments = aligner(speech, text[0].split())

In [96]:
print(segments)

utt_0000 utt 0.36 0.78 -0.0001 mina
utt_0001 utt 0.78 1.19 -0.0003 tahaksin
utt_0002 utt 1.19 1.59 -0.0017 homme
utt_0003 utt 1.67 2.19 -0.0001 täna
utt_0004 utt 3.24 3.76 -0.0037 ja
utt_0005 utt 3.76 4.28 -0.0000 homme
utt_0006 utt 5.61 6.13 -0.0001 kui
utt_0007 utt 6.17 6.69 -0.0009 saanud
utt_0008 utt 6.81 7.33 -0.0018 on
utt_0009 utt 7.98 8.50 -0.0862 kui
utt_0010 utt 8.50 9.34 -0.1062 krampsumas
utt_0011 utt 9.34 9.54 -0.1183 ise
utt_0012 utt 9.54 10.07 -0.2033 veiki
utt_0013 utt 10.07 10.31 -0.1041 panna



## Get timestamps with some correction

In [97]:
def get_timestamps(aligner, speech, text, time_correction=0.2):
    tokens=text.split()
    segments = aligner(speech, tokens)
    df=pd.DataFrame(segments.segments)
    df.columns=['start', 'end', 'confidence']
    df['start']=df.start+time_correction
    df['end']=df.end+time_correction
    df['words']=tokens
    return df

In [128]:
torch.set_num_threads(5)

In [131]:
speech, rate = soundfile.read("example_audio/oden_kypsis16k_subset2.wav")
assert rate == 16000

%time text, *_ = speech2text(speech)

CPU times: user 14.4 s, sys: 89.6 ms, total: 14.5 s
Wall time: 2.9 s


In [132]:
!soxi example_audio/oden_kypsis16k_subset2.wav


Input File     : 'example_audio/oden_kypsis16k_subset2.wav'
Channels       : 1
Sample Rate    : 16000
Precision      : 16-bit
Duration       : 00:00:09.19 = 146983 samples ~ 688.983 CDDA sectors
File Size      : 294k
Bit Rate       : 256k
Sample Encoding: 16-bit Signed Integer PCM



In [108]:
%time df_times=get_timestamps(aligner, speech, text[0])

CPU times: user 474 ms, sys: 30.2 ms, total: 504 ms
Wall time: 501 ms


In [109]:
df_times.head(20)

start       end  confidence           words
0   0.260154  0.661184   -0.107317          klikid
1   0.661184  0.821596   -0.001331            neid
2   0.822883  1.784067   -0.002136        allserva
3   1.784067  1.984582   -0.041078         tekivad
4   2.547310  3.067362   -0.008251            need
5   3.067362  4.029833   -0.007814   lubaküpsiseid
6   4.752973  5.273025   -0.000333             mis
7   5.273025  5.413385   -0.063720              on
8   5.413385  5.553745   -0.000231            nagu
9   5.553745  5.834466   -0.000573          ilusti
10  5.834466  6.115187   -0.001930          kohati
11  6.236783  7.037555   -0.004937        tõlgitud
12  7.037555  7.238070   -0.001092           eesti
13  7.238070  7.679202   -0.003088          keelde
14  7.800798  8.320850   -0.001126             see
15  8.320850  8.601571   -0.033408            idee
16  8.601571  9.363527   -0.032846  arusaadavamaks
17  9.363527  9.584093   -0.390966              ma
18  9.584093  9.764557   -0.053868            tean
19  9.764557  9.924968   -0.000163              et